### Read Data

In [22]:
import pandas as pd 
all_data = pd.read_csv("dataset.csv") 
all_data.head()

review sentiment
0  One of the other reviewers has mentioned that ...  positive
1  A wonderful little production. <br /><br />The...  positive
2  I thought this was a wonderful way to spend ti...  positive
3  Basically there's a family where a little boy ...  negative
4  Petter Mattei's "Love in the Time of Money" is...  positive

In [23]:
import numpy as np
all_data_x = all_data.loc[:, ["review"]].values
all_data_y = all_data.loc[:, ["sentiment"]].values
print("All Data X Shape: ",all_data_x.shape)
print("All Data Y Shape: ",all_data_y.shape)



All Data X Shape:  (50000, 1)
All Data Y Shape:  (50000, 1)


### Data Preprocessing and Creating Labels

In [24]:
def separateClasses(all_data_x, all_data_y):
    
    x_positive = []
    y_positive = []
    x_negative = []
    y_negative = []
    
    for i in range(all_data_y.shape[0]):
        
        if all_data_y[i] == "positive":
            
            x_positive.append(all_data_x[i])
            y_positive.append(all_data_y[i])
            
            
        if all_data_y[i] == "negative":
            
            x_negative.append(all_data_x[i])
            y_negative.append(all_data_y[i])
        
        
    return x_positive, y_positive, x_negative, y_negative
    
x_positive, y_positive, x_negative, y_negative = separateClasses(all_data_x, all_data_y)

x_positive = np.array(x_positive)
y_positive = np.array(y_positive)
x_negative = np.array(x_negative)
y_negative = np.array(y_negative)

print("Positive x shape: ",x_positive.shape)
print("Positive y shape: ",y_positive.shape)
print("Negative x shape: ",x_negative.shape)
print("Negative y shape: ",y_negative.shape)

Positive x shape:  (25000, 1)
Positive y shape:  (25000, 1)
Negative x shape:  (25000, 1)
Negative y shape:  (25000, 1)


In [25]:
# positive 1 0
# negative 0 1
positive_label = []
negative_label = []
for i in range(25000):
    
    positive =  np.array([[1,0]])
    negative = np.array([[0,1]])
    
    positive_label.append(positive)
    negative_label.append(negative)

y_positive = np.array(positive_label)
y_negative = np.array(negative_label)
y_positive = y_positive[:,-1,:]
y_negative = y_negative[:,-1,:]

limit = 1000
x_positive = x_positive[:limit ]
x_negative = x_negative[:limit ]
y_positive = y_positive[:limit ]
y_negative = y_negative[:limit ]


print("Positive x shape: ",x_positive.shape)
print("Positive y shape: ",y_positive.shape)
print("Negative x shape: ",x_negative.shape)
print("Negative y shape: ",y_negative.shape)



x_data = np.concatenate((x_positive, x_negative), axis = 0)
y_data = np.concatenate((y_positive, y_negative), axis = 0)



print("X Data Shape:",x_data.shape)
print("Y Data Shape:",y_data.shape)

Positive x shape:  (1000, 1)
Positive y shape:  (1000, 2)
Negative x shape:  (1000, 1)
Negative y shape:  (1000, 2)
X Data Shape: (2000, 1)
Y Data Shape: (2000, 2)


### Text Cleaning

In [26]:
#Text Cleaning
from string import punctuation, digits

input = [np.array_str(value) for value in list(x_data)] 

converter = str.maketrans('', '', punctuation)
input = [value.translate(converter) for value in input] 

converter = str.maketrans('', '', digits)
input = [value.translate(converter) for value in input] 

input = [value.lower().split(" ") for value in input] 

### Don't Clean

In [27]:
#input = [np.array_str(value).lower().split(" ") for value in list(x_data)] 

### Word2Vec Embeddings
Source: https://www.kaggle.com/pierremegret/gensim-word2vec-tutorial
Word2vec input: string list

In [28]:
def Word2vecFeatureExtraction(input, output_size, epoch, model_name):
    from gensim.models import Word2Vec
    import multiprocessing
    from time import time  # To time our operations
    
    model = Word2Vec(min_count=1,window=2,size=output_size,sample=6e-5,alpha=0.03,min_alpha=0.0007,negative=20,workers=4)
    
    t = time()
    model.build_vocab(input, progress_per=10000)
    words = list(model.wv.vocab)
    print("Vocab. length: ",len(words))
    print('Time to build vocab: {} mins'.format(round((time() - t) / 60, 2)))
    
    t = time()

    model.train(input, total_examples = model.corpus_count, epochs = epoch, report_delay=1)
    model.save("epoch_" + str(epoch) + "_output_size_"+str(output_size)+"_"+ model_name + ".bin")
    print('Time to train the model: {} mins'.format(round((time() - t) / 60, 2)))
    
    tokens_lengths = [len(model.wv[value]) for value in input]
    print("Maximum token length in each samples: ", max(tokens_lengths))
    
    features = [model.wv[value] for value in input]
    #model = Word2Vec.load(model_name)
    
    return features

def paddedFeatures(features, target_dimension, position):
    import numpy as np
    padded_features = []
    
    if position == "right":
        for sample in features:
            zeros = np.zeros((target_dimension-sample.shape[0],sample.shape[1]))
            padded_sample = np.concatenate((sample,zeros),axis=0)
            padded_features.append(padded_sample)
             
    if position == "left":
        for sample in features:
            zeros = np.zeros((target_dimension-sample.shape[0],sample.shape[1]))
            padded_sample = np.concatenate((zeros,sample),axis=0)
            padded_features.append(padded_sample)
            
    print("Padding is done.")
            
    return padded_features

input = Word2vecFeatureExtraction(input, 10 , 1, "1")
input = paddedFeatures(input, target_dimension=1528, position = "right")

Vocab. length:  30170
Time to build vocab: 0.01 mins
Time to train the model: 0.01 mins
Maximum token length in each samples:  1527
Padding is done.


### Test Train Split

In [29]:
"""from sklearn.model_selection import train_test_split
x_train, x_test, y_train, y_test = train_test_split(np.array(input), y_data, test_size= 0.2, random_state=42)
x_train = x_train.reshape((40000,1))
x_test = x_test.reshape((10000,1))
print("X Train Shape:",x_train.shape)
print("Y Train Shape:",y_train.shape)
print("X Test Shape:",x_test.shape)
print("Y Test Shape:",y_test.shape)"""

'from sklearn.model_selection import train_test_split\nx_train, x_test, y_train, y_test = train_test_split(np.array(input), y_data, test_size= 0.2, random_state=42)\nx_train = x_train.reshape((40000,1))\nx_test = x_test.reshape((10000,1))\nprint("X Train Shape:",x_train.shape)\nprint("Y Train Shape:",y_train.shape)\nprint("X Test Shape:",x_test.shape)\nprint("Y Test Shape:",y_test.shape)'

In [30]:
import torch.nn as nn
import torch

x_train = np.array(input)
y_train = y_data
print(x_train.shape,y_train.shape)
print(type(x_train),type(y_train))
print(type(x_train[0]),type(y_train[0]))

from sklearn.utils import shuffle
x_train, y_train = shuffle(x_train, y_train, random_state=0)

x_train = torch.from_numpy(x_train).float()
y_train = torch.from_numpy(y_train).float()

(2000, 1528, 10) (2000, 2)
<class 'numpy.ndarray'> <class 'numpy.ndarray'>
<class 'numpy.ndarray'> <class 'numpy.ndarray'>


In [ ]:
import torch.nn as nn
from time import time

class LSTM(nn.Module):
    def __init__(self, input_size=10, hidden_layer_size=50, output_size=2):
        super().__init__()
        
        self.batch = 1
        self.num_layers = 1
        self.hidden_layer_size = 50

        self.lstm = nn.LSTM(input_size, hidden_layer_size, batch_first = True, dropout = 0.2)

        self.linear = nn.Linear(hidden_layer_size, hidden_layer_size)
        
        self.linear2 = nn.Linear(hidden_layer_size, output_size)

        self.hidden_cell = (torch.zeros(self.num_layers,self.batch,self.hidden_layer_size),
                            torch.zeros(self.num_layers,self.batch,self.hidden_layer_size))

    def forward(self, input_seq):
        
        #print("Input Shape: ", input_seq.shape)
    
        input_seq = input_seq.view(1,1528,10)
        #print("Expanded LSTM Input Shape: ", input_seq.shape)
        
        lstm_out, self.hidden_cell = self.lstm(input_seq, self.hidden_cell)
        #print("LSTM output shape: ",lstm_out.shape)
        
        #print("Linear Layer Input Shape: ",lstm_out.view(-1,self.hidden_layer_size).shape)
        predictions = self.linear(lstm_out.view(-1,self.hidden_layer_size))
        
        predictions = self.linear2(predictions)
        
        #print("Predictions shape: ",predictions.shape)
        #print("Returned values for loss", predictions[-1].shape)
        y = torch.nn.functional.softmax(predictions[-1], dim=0)
        print("*************************************************")
        return y
    

model = LSTM()
loss_function = nn.MSELoss()
optimizer = torch.optim.Adam(model.parameters(), lr = 0.001)
print(model)

epochs = 20

loss_list = []
t = time()
for i in range(epochs):
    k = 0
    for k in range(y_train.shape[0]):
        print("data: ",k)
        optimizer.zero_grad()
        
       
        model.hidden_cell = (torch.zeros(model.num_layers, model.batch, model.hidden_layer_size),
                        torch.zeros(model.num_layers, model.batch, model.hidden_layer_size))

        y_pred = model(x_train[k])
        
        print(y_pred)
        print(y_train[k])
        
        
        single_loss = loss_function(y_pred, y_train[k])
        print(single_loss.item())
        single_loss.backward()
        optimizer.step()

        loss_list.append(single_loss.item())
        print("Toplam geçen süre:",round((time() - t) / 60, 2)," dakika")
        print(f'epoch: {i:3} loss: {single_loss.item():10.8f}')
        print("*************************************************")
    
    checkpoint = {'model': LSTM(),'state_dict': model.state_dict(),'optimizer' : optimizer.state_dict()}
    print("Average loss: ",sum(loss_list)/y_train.shape[0])
    torch.save(checkpoint, 'Epoch {} Checkpoint.pth'.format(i))
    print("\nModel kaydedildi.\n")
    



LSTM(
  (lstm): LSTM(10, 50, batch_first=True, dropout=0.2)
  (linear): Linear(in_features=50, out_features=50, bias=True)
  (linear2): Linear(in_features=50, out_features=2, bias=True)
)
data:  0
*************************************************
tensor([0.4822, 0.5178], grad_fn=<SoftmaxBackward>)
tensor([1., 0.])
0.2680979073047638
Toplam geçen süre: 0.01  dakika
epoch:   0 loss: 0.26809791
*************************************************
data:  1
*************************************************
tensor([0.4898, 0.5102], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.23985907435417175
Toplam geçen süre: 0.03  dakika
epoch:   0 loss: 0.23985907
*************************************************
data:  2
*************************************************
tensor([0.4895, 0.5105], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.23965252935886383
Toplam geçen süre: 0.04  dakika
epoch:   0 loss: 0.23965253
*************************************************
data:  3
******************************

*************************************************
tensor([0.4291, 0.5709], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.18412356078624725
Toplam geçen süre: 0.46  dakika
epoch:   0 loss: 0.18412356
*************************************************
data:  32
*************************************************
tensor([0.4260, 0.5740], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.1814657598733902
Toplam geçen süre: 0.47  dakika
epoch:   0 loss: 0.18146576
*************************************************
data:  33
*************************************************
tensor([0.4223, 0.5777], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.17833048105239868
Toplam geçen süre: 0.49  dakika
epoch:   0 loss: 0.17833048
*************************************************
data:  34
*************************************************
tensor([0.4180, 0.5820], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.17472773790359497
Toplam geçen süre: 0.5  dakika
epoch:   0 loss: 0.17472774
**************************

*************************************************
tensor([0.4365, 0.5635], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.19053643941879272
Toplam geçen süre: 0.94  dakika
epoch:   0 loss: 0.19053644
*************************************************
data:  64
*************************************************
tensor([0.4359, 0.5641], grad_fn=<SoftmaxBackward>)
tensor([1., 0.])
0.3181679844856262
Toplam geçen süre: 0.95  dakika
epoch:   0 loss: 0.31816798
*************************************************
data:  65
*************************************************
tensor([0.4361, 0.5639], grad_fn=<SoftmaxBackward>)
tensor([1., 0.])
0.3179296553134918
Toplam geçen süre: 0.96  dakika
epoch:   0 loss: 0.31792966
*************************************************
data:  66
*************************************************
tensor([0.4371, 0.5629], grad_fn=<SoftmaxBackward>)
tensor([1., 0.])
0.3169093728065491
Toplam geçen süre: 0.98  dakika
epoch:   0 loss: 0.31690937
***************************

*************************************************
tensor([0.4823, 0.5177], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.23263108730316162
Toplam geçen süre: 1.41  dakika
epoch:   0 loss: 0.23263109
*************************************************
data:  96
*************************************************
tensor([0.4823, 0.5177], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.2326214760541916
Toplam geçen süre: 1.43  dakika
epoch:   0 loss: 0.23262148
*************************************************
data:  97
*************************************************
tensor([0.4817, 0.5183], grad_fn=<SoftmaxBackward>)
tensor([1., 0.])
0.2686239182949066
Toplam geçen süre: 1.44  dakika
epoch:   0 loss: 0.26862392
*************************************************
data:  98
*************************************************
tensor([0.4818, 0.5182], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.2321358025074005
Toplam geçen süre: 1.46  dakika
epoch:   0 loss: 0.23213580
***************************

*************************************************
tensor([0.4865, 0.5135], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.23672190308570862
Toplam geçen süre: 1.9  dakika
epoch:   0 loss: 0.23672190
*************************************************
data:  128
*************************************************
tensor([0.4868, 0.5132], grad_fn=<SoftmaxBackward>)
tensor([1., 0.])
0.2633693516254425
Toplam geçen süre: 1.91  dakika
epoch:   0 loss: 0.26336935
*************************************************
data:  129
*************************************************
tensor([0.4876, 0.5124], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.2378021776676178
Toplam geçen süre: 1.93  dakika
epoch:   0 loss: 0.23780218
*************************************************
data:  130
*************************************************
tensor([0.4878, 0.5122], grad_fn=<SoftmaxBackward>)
tensor([1., 0.])
0.2623165547847748
Toplam geçen süre: 1.95  dakika
epoch:   0 loss: 0.26231655
*************************

...

Toplam geçen süre: 237.08  dakika
epoch:   7 loss: 0.27392334
*************************************************
data:  1483
*************************************************
tensor([0.4766, 0.5234], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.22718872129917145
Toplam geçen süre: 237.09  dakika
epoch:   7 loss: 0.22718872
*************************************************
data:  1484
*************************************************
tensor([0.4763, 0.5237], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.2268933355808258
Toplam geçen süre: 237.11  dakika
epoch:   7 loss: 0.22689334
*************************************************
data:  1485
*************************************************
tensor([0.4757, 0.5243], grad_fn=<SoftmaxBackward>)
tensor([1., 0.])
0.27487000823020935
Toplam geçen süre: 237.12  dakika
epoch:   7 loss: 0.27487001
*************************************************
data:  1486
*************************************************
tensor([0.4755, 0.5245], grad_fn=<Soft

*************************************************
tensor([0.4734, 0.5266], grad_fn=<SoftmaxBackward>)
tensor([1., 0.])
0.277289479970932
Toplam geçen süre: 237.56  dakika
epoch:   7 loss: 0.27728948
*************************************************
data:  1515
*************************************************
tensor([0.4738, 0.5262], grad_fn=<SoftmaxBackward>)
tensor([1., 0.])
0.2768740653991699
Toplam geçen süre: 237.58  dakika
epoch:   7 loss: 0.27687407
*************************************************
data:  1516
*************************************************
tensor([0.4745, 0.5255], grad_fn=<SoftmaxBackward>)
tensor([1., 0.])
0.27612513303756714
Toplam geçen süre: 237.59  dakika
epoch:   7 loss: 0.27612513
*************************************************
data:  1517
*************************************************
tensor([0.4755, 0.5245], grad_fn=<SoftmaxBackward>)
tensor([1., 0.])
0.2751026451587677
Toplam geçen süre: 237.61  dakika
epoch:   7 loss: 0.27510265
**************

Toplam geçen süre: 238.04  dakika
epoch:   7 loss: 0.23453279
*************************************************
data:  1546
*************************************************
tensor([0.4842, 0.5158], grad_fn=<SoftmaxBackward>)
tensor([1., 0.])
0.2660064101219177
Toplam geçen süre: 238.06  dakika
epoch:   7 loss: 0.26600641
*************************************************
data:  1547
*************************************************
tensor([0.4844, 0.5156], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.2346397489309311
Toplam geçen süre: 238.07  dakika
epoch:   7 loss: 0.23463975
*************************************************
data:  1548
*************************************************
tensor([0.4844, 0.5156], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.2345988005399704
Toplam geçen süre: 238.09  dakika
epoch:   7 loss: 0.23459880
*************************************************
data:  1549
*************************************************
tensor([0.4841, 0.5159], grad_fn=<Softma

*************************************************
tensor([0.4745, 0.5255], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.22516284883022308
Toplam geçen süre: 238.53  dakika
epoch:   7 loss: 0.22516285
*************************************************
data:  1578
*************************************************
tensor([0.4739, 0.5261], grad_fn=<SoftmaxBackward>)
tensor([1., 0.])
0.27682462334632874
Toplam geçen süre: 238.55  dakika
epoch:   7 loss: 0.27682462
*************************************************
data:  1579
*************************************************
tensor([0.4736, 0.5264], grad_fn=<SoftmaxBackward>)
tensor([1., 0.])
0.277112752199173
Toplam geçen süre: 238.56  dakika
epoch:   7 loss: 0.27711275
*************************************************
data:  1580
*************************************************
tensor([0.4737, 0.5263], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.22435463964939117
Toplam geçen süre: 238.58  dakika
epoch:   7 loss: 0.22435464
************

Toplam geçen süre: 239.01  dakika
epoch:   7 loss: 0.22317231
*************************************************
data:  1609
*************************************************
tensor([0.4731, 0.5269], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.22382360696792603
Toplam geçen süre: 239.02  dakika
epoch:   7 loss: 0.22382361
*************************************************
data:  1610
*************************************************
tensor([0.4734, 0.5266], grad_fn=<SoftmaxBackward>)
tensor([0., 1.])
0.224150151014328
Toplam geçen süre: 239.04  dakika
epoch:   7 loss: 0.22415015
*************************************************
data:  1611
*************************************************
tensor([0.4735, 0.5265], grad_fn=<SoftmaxBackward>)
tensor([1., 0.])
0.2772107720375061
Toplam geçen süre: 239.05  dakika
epoch:   7 loss: 0.27721077
*************************************************
data:  1612
*************************************************
tensor([0.4738, 0.5262], grad_fn=<Softma

In [ ]:
16.25 başlama saati